##### Copyright 2018 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# 自动重写 TF 1.x 和 compat.v1 API 符号

<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://tensorflow.google.cn/guide/migrate/upgrade"><img src="https://tensorflow.google.cn/images/tf_logo_32px.png">在 TensorFlow.org 上查看</a>   </td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/migrate/upgrade.ipynb"><img src="https://tensorflow.google.cn/images/colab_logo_32px.png">在 Google Colab 运行</a>
</td>
  <td>     <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/migrate/upgrade.ipynb"><img src="https://tensorflow.google.cn/images/GitHub-Mark-32px.png">在 Github 上查看源代码</a>
</td>
  <td>     <a target="_blank" href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/zh-cn/guide/migrate/upgrade.ipynb"><img src="https://tensorflow.google.cn/images/download_logo_32px.png">下载笔记本</a>
</td>
</table>


TensorFlow 2.x 包含 TF 1.x 和 `tf.compat.v1` API 的许多 API 更改，例如重新排序了参数，重命名了符号，更改了参数的默认值。手动执行所有这些修改可能很乏味，而且很容易出错。为了简化更改，尽可能让您无缝过渡到 TF 2.x，TensorFlow 团队创建了 `tf_upgrade_v2` 效用函数，帮助您将旧版代码转换至新的 API。

注：TensorFlow 1.13 和更高版本（包括所有 TF 2.0 构建）会自动安装 `tf_upgrade_v2`。

典型的用法如下：

<pre class="devsite-terminal devsite-click-to-copy prettyprint lang-bsh">
tf_upgrade_v2 \
  --intree my_project/ \
  --outtree my_project_v2/ \
  --reportfile report.txt
</pre>

将现有 TensorFlow 1.x Python 脚本转换为 TensorFlow 2.x 脚本可以加快升级流程。

尽管许多 API 无法自动迁移，但转换脚本会自动执行许多机械 API 转换。它也无法使您的代码与 TF2 行为和 API 完全兼容。因此，这只是您迁移之旅的一部分。

## 兼容性模块

某些 API 符号不能简单地通过使用字符串替换来升级。那些无法自动升级的符号将被映射到它们在 `compat.v1` 模块中的位置。此模块将 `tf.foo` 等 TF 1.x 符号替换为对应的 `tf.compat.v1.foo` 引用。如果您已经通过 `import tensorflow.compat.v1 as tf` 导入 TF 来使用 `compat.v1` API，`tf_upgrade_v2` 脚本会尝试尽可能将这些用法转换为非兼容 API。请注意，尽管有些 `compat.v1` API 与 TF2.x 行为兼容，但许多 API 不兼容。因此，建议尽快手动检查替换并将它们迁移到 `tf.*` 命名空间而不是 `tf.compat.v1` 命名空间中的新 API。

由于在 TensorFlow 2.x 模块弃用（例如，`tf.flags` 和 `tf.contrib`），所以切换到 `compat.v1` 无法解决某些更改。升级此代码可能需要其他库（例如，[`absl.flags`](https://github.com/abseil/abseil-py)）或切换到 [tensorflow/addons](http://www.github.com/tensorflow/addons) 中的软件包。


## 推荐的升级流程

本指南的剩余部分将演示如何使用符号重写脚本。虽然此脚本易于使用，但我们仍强烈建议按照以下流程使用脚本：

1. **单元测试**：确保要升级的代码包含具有合理覆盖率的单元测试套件。这是 Python 代码，该语言并不会帮助您避免各种类型的错误。同时还要确保已升级所有依赖项，使其与 TensorFlow 2.x 兼容。

2. **安装 TensorFlow 1.15**：将 TensorFlow 升级到最新的 TensorFlow 1.x 版本（最低为 1.15 版本）。其中包括 `tf.compat.v2` 中的最终 TensorFlow 2.0 API。

3. **使用 1.15 版本进行测试**：确保此时可以通过单元测试。在升级过程中，您将反复进行测试，因此，从可以正常运行的代码开始非常重要。

4. **运行升级脚本**：对整个源代码树运行 `tf_upgrade_v2`（已包含测试）。这样可将代码升级为仅使用 TensorFlow 2.0 中提供的符号的格式。被弃用的符号将通过 `tf.compat.v1` 进行访问。最终需要人工检查这些升级，但不是现在。

5. **使用 TensorFlow 1.15 运行转换的测试**：代码在 TensorFlow 1.15 中应该仍可以正常运行。再次运行单元测试。测试在此时产生任何错误都意味着升级脚本存在错误。[请通知我们](https://github.com/tensorflow/tensorflow/issues)。

6. **检查更新报告中的警告和错误**：该脚本会编写一个对需要复查的转换或需要执行的人工操作进行解释的报告文件。例如：contrib 的所有剩余实例需要通过人工移除。请查阅 [RFC 中的详细说明](https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md)。

7. **安装 TensorFlow 2.x**：此时切换到 TensorFlow 2.x 二进制文件应当是安全的，即使您正在运行旧版行为

8. **使用 `v1.disable_v2_behavior` 进行测试**：使用测试主函数中的 `v1.disable_v2_behavior()` 重新运行测试产生的结果应与在 1.15 下运行时产生的结果相同。

9. **启用 V2 行为**：现在，您的测试使用 TF2 二进制文件工作，现在可以开始迁移代码以避免 `tf.estimator` 并仅使用受支持的 TF2 行为（不停用 TF2 行为）。请参阅[迁移指南](https://tensorflow.org/guide/migrate)以了解详情。

## 使用符号重写 `tf_upgrade_v2` 脚本


### 安装

首先，请确保已安装 TensorFlow 2.x。

In [2]:
import tensorflow as tf

print(tf.__version__)

2022-12-14 21:00:28.410584: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:28.410673: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:28.410683: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


2.11.0


克隆 [tensorflow/models](https://github.com/tensorflow/models)s git 仓库，以便获得要测试的一些代码：

In [3]:
!git clone --branch r1.13.0 --depth 1 https://github.com/tensorflow/models

Cloning into 'models'...


remote: Enumerating objects: 2927, done.
remote: Counting objects: 100% (2927/2927), done.


remote: Compressing objects: 100% (2428/2428), done.


remote: Total 2927 (delta 503), reused 2114 (delta 424), pack-reused 0
Receiving objects: 100% (2927/2927), 369.04 MiB | 54.42 MiB/s, done.
Resolving deltas: 100% (503/503), done.


Updating files: 100% (2768/2768), done.


### 读取帮助

安装 TensorFlow 时应该已安装该脚本。下面是内置帮助命令：

In [4]:
!tf_upgrade_v2 -h

2022-12-14 21:00:42.454774: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:42.454864: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:42.454875: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


usage: tf_upgrade_v2 [-h] [--infile INPUT_FILE] [--outfile OUTPUT_FILE]
                     [--intree INPUT_TREE] [--outtree OUTPUT_TREE]
                     [--copyotherfiles COPY_OTHER_FILES] [--inplace]
                     [--no_import_rename] [--no_upgrade_compat_v1_import]
                     [--reportfile REPORT_FILENAME] [--mode {DEFAULT,SAFETY}]
                     [--print_all]

Convert a TensorFlow Python file from 1.x to 2.0

Simple usage:
  tf_upgrade_v2.py --infile foo.py --outfile bar.py
  tf_upgrade_v2.py --infile foo.ipynb --outfile bar.ipynb
  tf_upgrade_v2.py --intree ~/code/old --outtree ~/code/new

optional arguments:
  -h, --help            show this help message and exit
  --infile INPUT_FILE   If converting a single file, the name of the file to
                        convert
  --outfile OUTPUT_FILE
                        If converting a single file, the output filename.
  --intree INPUT_TREE   If converting a whole tree of files, the directory to
        

### TF1 代码示例

下面是一个简单的 TensorFlow 1.0 脚本：

In [5]:
!head -n 65 models/samples/cookbook/regression/custom_regression.py | tail -n 10

  # Calculate loss using mean squared error
  average_loss = tf.losses.mean_squared_error(labels, predictions)

  # Pre-made estimators use the total_loss instead of the average,
  # so report total_loss for compatibility.
  batch_size = tf.shape(labels)[0]
  total_loss = tf.to_float(batch_size) * average_loss

  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = params.get("optimizer", tf.train.AdamOptimizer)


对于安装的 TensorFlow 2.x，它不会运行：

In [6]:
!(cd models/samples/cookbook/regression && python custom_regression.py)

2022-12-14 21:00:45.033189: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:45.033277: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:45.033287: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


Traceback (most recent call last):
  File "/tmpfs/src/temp/site/zh-cn/guide/migrate/models/samples/cookbook/regression/custom_regression.py", line 162, in <module>
    tf.logging.set_verbosity(tf.logging.INFO)
AttributeError: module 'tensorflow' has no attribute 'logging'


### 单个文件

该脚本可以对单个 Python 文件运行：

In [7]:
!tf_upgrade_v2 \
  --infile models/samples/cookbook/regression/custom_regression.py \
  --outfile /tmp/custom_regression_v2.py

2022-12-14 21:00:47.430391: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:47.430480: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:47.430490: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


INFO line 38:8: Renamed 'tf.feature_column.input_layer' to 'tf.compat.v1.feature_column.input_layer'
INFO line 43:10: Renamed 'tf.layers.dense' to 'tf.compat.v1.layers.dense'
INFO line 46:17: Renamed 'tf.layers.dense' to 'tf.compat.v1.layers.dense'
INFO line 57:17: tf.losses.mean_squared_error requires manual check. tf.losses have been replaced with object oriented versions in TF 2.0 and after. The loss function calls have been converted to compat.v1 for backward compatibility. Please update these calls to the TF 2.0 versions.
INFO line 57:17: Renamed 'tf.losses.mean_squared_error' to 'tf.compat.v1.losses.mean_squared_error'
INFO line 61:15: Added keywords to args of function 'tf.shape'
INFO line 62:15: Changed tf.to_float call to tf.cast(..., dtype=tf.float32).
INFO line 65:40: Renamed 'tf.train.AdamOptimizer' to 'tf.compat.v1.train.AdamOptimizer'
INFO line 68:39: Renamed 'tf.train.get_global_step' to 'tf.compat.v1.train.get_global_step'
INFO line 83:9: tf.metrics.root_mean_squared_er

TensorFlow 2.0 Upgrade Script
-----------------------------
Converted 1 files
Detected 0 issues that require attention
--------------------------------------------------------------------------------


Make sure to read the detailed log 'report.txt'



如果无法找到修正代码问题的方法，该脚本会打印错误消息。 

### 目录树

典型项目（包括下面的简单示例）会使用远不止一个文件。通常需要更新整个软件包，因此该脚本也可以对目录树运行：

In [8]:
# update the .py files and copy all the other files to the outtree
!tf_upgrade_v2 \
    --intree models/samples/cookbook/regression/ \
    --outtree regression_v2/ \
    --reportfile tree_report.txt

2022-12-14 21:00:49.884020: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:49.884109: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:00:49.884119: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


INFO line 40:7: Renamed 'tf.test.mock' to 'tf.compat.v1.test.mock'


WARNING line 125:15: Changing dataset.make_one_shot_iterator() to tf.compat.v1.data.make_one_shot_iterator(dataset). Please check this transformation.

INFO line 58:10: tf.estimator.LinearRegressor: Default value of loss_reduction has been changed to SUM_OVER_BATCH_SIZE; inserting old default value tf.keras.losses.Reduction.SUM.

INFO line 101:2: Renamed 'tf.logging.set_verbosity' to 'tf.compat.v1.logging.set_verbosity'
INFO line 101:27: Renamed 'tf.logging.INFO' to 'tf.compat.v1.logging.INFO'
INFO line 102:2: Renamed 'tf.app.run' to 'tf.compat.v1.app.run'
INFO line 72:10: tf.estimator.DNNRegressor: Default value of loss_reduction has been changed to SUM_OVER_BATCH_SIZE; inserting old default value tf.keras.losses.Reduction.SUM.

INFO line 96:2: Renamed 'tf.logging.set_verbosity' to 'tf.compat.v1.logging.set_verbosity'
INFO line 96:27: Renamed 'tf.logging.INFO' to 'tf.compat.v1.logging.INFO'
INFO line 97:2: Renamed 'tf.app.run' to 'tf.compat.v1.app.run'


INFO line 82:10: tf.estimator.LinearRegressor: Default value of loss_reduction has been changed to SUM_OVER_BATCH_SIZE; inserting old default value tf.keras.losses.Reduction.SUM.

INFO line 105:2: Renamed 'tf.logging.set_verbosity' to 'tf.compat.v1.logging.set_verbosity'
INFO line 105:27: Renamed 'tf.logging.INFO' to 'tf.compat.v1.logging.INFO'
INFO line 106:2: Renamed 'tf.app.run' to 'tf.compat.v1.app.run'
INFO line 38:8: Renamed 'tf.feature_column.input_layer' to 'tf.compat.v1.feature_column.input_layer'
INFO line 43:10: Renamed 'tf.layers.dense' to 'tf.compat.v1.layers.dense'
INFO line 46:17: Renamed 'tf.layers.dense' to 'tf.compat.v1.layers.dense'
INFO line 57:17: tf.losses.mean_squared_error requires manual check. tf.losses have been replaced with object oriented versions in TF 2.0 and after. The loss function calls have been converted to compat.v1 for backward compatibility. Please update these calls to the TF 2.0 versions.
INFO line 57:17: Renamed 'tf.losses.mean_squared_error' 

注意关于 `dataset.make_one_shot_iterator` 函数的一条警告。

现在，对于 TensorFlow 2.x，该脚本已经可以发挥作用：

请注意，由于 TF 1.15 中包含 `tf.compat.v1` 模块，转换的脚本在 TensorFlow 1.15 中也可以运行。

In [9]:
!(cd regression_v2 && python custom_regression.py 2>&1) | tail

I1214 21:01:01.809502 140703740618560 estimator.py:2083] Saving dict for global step 1000: global_step = 1000, loss = 546.7986, rmse = 3.3751497
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 1000: /tmpfs/tmp/tmpk1ymuugp/model.ckpt-1000
I1214 21:01:01.853601 140703740618560 estimator.py:2143] Saving 'checkpoint_path' summary for global step 1000: /tmpfs/tmp/tmpk1ymuugp/model.ckpt-1000
Tensor("IteratorGetNext:25", shape=(None,), dtype=float64, device=/device:CPU:0)
Tensor("Squeeze:0", shape=(None,), dtype=float32)

********************************************************************************

RMS error for the test set: $3375



## 详细报告

该脚本还会报告一个详细更改的列表。在本例中，它发现了一个可能不安全的转换，因此在文件顶部包含了一条警告： 

In [10]:
!head -n 20 tree_report.txt

TensorFlow 2.0 Upgrade Script
-----------------------------
Converted 7 files
Detected 1 issues that require attention
--------------------------------------------------------------------------------
--------------------------------------------------------------------------------
File: models/samples/cookbook/regression/automobile_data.py
--------------------------------------------------------------------------------
models/samples/cookbook/regression/automobile_data.py:125:15: WARNING: Changing dataset.make_one_shot_iterator() to tf.compat.v1.data.make_one_shot_iterator(dataset). Please check this transformation.

Detailed log follows:

Input tree: 'models/samples/cookbook/regression/'
--------------------------------------------------------------------------------
Processing file 'models/samples/cookbook/regression/__init__.py'
 outputting to 'regression_v2/__init__.py'


再次注意关于 `Dataset.make_one_shot_iterator function` 函数的一条警告。

在其他情况下，对于比较重要的更改，输出会解释原因：

In [11]:
%%writefile dropout.py
import tensorflow as tf

d = tf.nn.dropout(tf.range(10), 0.2)
z = tf.zeros_like(d, optimize=False)

Writing dropout.py


In [12]:
!tf_upgrade_v2 \
  --infile dropout.py \
  --outfile dropout_v2.py \
  --reportfile dropout_report.txt > /dev/null

2022-12-14 21:01:04.210481: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:01:04.210578: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:01:04.210597: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


In [13]:
!cat dropout_report.txt

TensorFlow 2.0 Upgrade Script
-----------------------------
Converted 1 files
Detected 0 issues that require attention
--------------------------------------------------------------------------------
Detailed log follows:

--------------------------------------------------------------------------------
Processing file 'dropout.py'
 outputting to 'dropout_v2.py'
--------------------------------------------------------------------------------

3:4: INFO: Changing keep_prob arg of tf.nn.dropout to rate, and recomputing value.

4:4: INFO: Renaming tf.zeros_like to tf.compat.v1.zeros_like because argument optimize is present. tf.zeros_like no longer takes an optimize argument, and behaves as if optimize=True. This call site specifies something other than optimize=True, so it was converted to compat.v1.
--------------------------------------------------------------------------------



以下是经过修改的文件内容，请注意脚本是如何通过添加参数名来处理移动和重命名的参数的：

In [14]:
!cat dropout_v2.py

import tensorflow as tf

d = tf.nn.dropout(tf.range(10), rate=1 - (0.2))
z = tf.compat.v1.zeros_like(d, optimize=False)


更大的项目可能会包含一些错误。例如，转换 deeplab 模型：

In [15]:
!tf_upgrade_v2 \
    --intree models/research/deeplab \
    --outtree deeplab_v2 \
    --reportfile deeplab_report.txt > /dev/null

2022-12-14 21:01:06.969746: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:01:06.969834: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:01:06.969844: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


它会生成输出文件：

In [16]:
!ls deeplab_v2

README.md	datasets	    input_preprocess.py        train.py
__init__.py	deeplab_demo.ipynb  local_test.sh	       utils
common.py	eval.py		    local_test_mobilenetv2.sh  vis.py
common_test.py	export_model.py     model.py
core		g3doc		    model_test.py


但是其中包含错误。该报告会帮助您找到确保代码可以正常运行所需要解决的错误。下面是前三个错误：

In [17]:
!cat deeplab_report.txt | grep -i models/research/deeplab | grep -i error | head -n 3

models/research/deeplab/export_model.py:25:7: ERROR: Using member tf.contrib.slim in deprecated module tf.contrib. tf.contrib.slim cannot be converted automatically. tf.contrib will not be distributed with TensorFlow 2.0, please consider an alternative in non-contrib TensorFlow, a community-maintained repository such as tensorflow/addons, or fork the required code.
models/research/deeplab/eval.py:28:7: ERROR: Using member tf.contrib.slim in deprecated module tf.contrib. tf.contrib.slim cannot be converted automatically. tf.contrib will not be distributed with TensorFlow 2.0, please consider an alternative in non-contrib TensorFlow, a community-maintained repository such as tensorflow/addons, or fork the required code.
models/research/deeplab/eval.py:146:8: ERROR: Using member tf.contrib.metrics.aggregate_metric_map in deprecated module tf.contrib. tf.contrib.metrics.aggregate_metric_map cannot be converted automatically. tf.contrib will not be distributed with TensorFlow 2.0, please co

## “安全”模式

该转换脚本还有一种介入度相对较低的 `SAFETY` 模式。在此模式下，只需更改导入来使用 `tensorflow.compat.v1` 模块：

In [18]:
!cat dropout.py

import tensorflow as tf

d = tf.nn.dropout(tf.range(10), 0.2)
z = tf.zeros_like(d, optimize=False)


In [19]:
!tf_upgrade_v2 --mode SAFETY --infile dropout.py --outfile dropout_v2_safe.py > /dev/null

2022-12-14 21:01:11.255934: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:01:11.256020: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:01:11.256031: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


In [20]:
!cat dropout_v2_safe.py

import tensorflow.compat.v1 as tf

d = tf.nn.dropout(tf.range(10), 0.2)
z = tf.zeros_like(d, optimize=False)


如您所见，这不会升级您的代码，但允许 TensorFlow 1 代码针对 TensorFlow 2 二进制文件运行。请注意，这并不意味着您的代码正在运行受支持的 TF 2.x 行为！

## 注意事项

- 在运行此脚本之前，不要手动更新代码的某些部分。尤其是，更改了参数顺序的函数（如 `tf.math.argmax` 或 `tf.batch_to_space`）会导致代码错误添加不正确映射现有代码匹配的关键字参数。

- 该脚本假定使用 `import tensorflow as tf` 或 `import tensorflow.compat.v1 as tf` 导入 `tensorflow`。

- 该脚本不会更改参数顺序，但是会将关键字参数添加到本身已更改参数顺序的函数。

- 请查阅 [tf2up.ml](https://github.com/lc0/tf2up)，找到一款方便的工具来升级 GitHub 仓库中的 Jupyter 笔记本和 Python 文件。

要报告升级脚本错误或提出功能请求，请在 [GitHub](https://github.com/tensorflow/tensorflow/issues) 上提交议题。